In [397]:
# Import appropriate modules
import pandas as pd
import datetime
import numpy as np
import yfinance as yf
from pathlib import Path
from datetime import datetime
import hvplot
import hvplot.pandas
# Import the finta Python library and the TA module
from finta import TA
from sklearn.metrics import classification_report
from sklearn.metrics import accuracy_score
from imblearn.over_sampling import RandomOverSampler
from sklearn.metrics import f1_score
from sklearn.metrics import recall_score
from pandas.tseries.offsets import DateOffset
# Import a new classifier from SKLearn
from sklearn.ensemble import AdaBoostClassifier
from sklearn.preprocessing import StandardScaler
from matplotlib import pyplot

In [398]:
# Initialize Global Variables that control the flow of the program
# Start date for the data
start_data_date = '2005-01-01'
# End date for the data
end_data_date = '2021-10-02'
# Define the training period for the model.
training_months = 120
# Do we do tuning of adaboost?
run_multiple_tuning_iterations = False
# The number of estimators to be used for the adaboost model
adaboost_estimators = 43

# Define some experimental technical indicator windows
# Define the short window
short_window = 50
# Define the long window
long_window = 200
# Define the general window
window = 120

In [399]:
# Define function to retrieve ticker daily return data from yahoo using ticker, start date and end date
def retrieve_yahoo_data_return(ticker = 'spy', start_date = start_data_date, end_date = end_data_date):
    try:
        # get data based on ticker
        yahoo_data = yf.Ticker(ticker)
        print(f"Processing Ticker {ticker}")
        # select data using start date and end data and calculate the daily return
        price_df = yahoo_data.history(start=start_date, end=end_date).Close.pct_change()
        price_df.name = ticker
        # if no data retrieved raise exception
        if price_df.shape[0] == 0:
            raise Exception("No Prices.")
        return price_df
    # handle exception
    except Exception as ex:
        print(f"Sorry, Data not available for '{ticker}': Exception is {ex}")

In [400]:
# Define function to retrieve ticker daily close data from yahoo using ticker, start date and end date
def retrieve_yahoo_data_close(ticker = 'spy', start_date = start_data_date, end_date = end_data_date):
    try:
        # get data based on ticker
        yahoo_data = yf.Ticker(ticker)
        print(f"Processing Ticker {ticker}")
        # select data using start date and end data and save the Close data
        price_df = yahoo_data.history(start=start_date, end=end_date).Close
        price_df.name = ticker
        # if no data retrieved raise exception
        if price_df.shape[0] == 0:
            raise Exception("No Prices.")
        return price_df
    # handle exception
    except Exception as ex:
        print(f"Sorry, Data not available for '{ticker}': Exception is {ex}")

In [401]:
# Define function to retrieve ticker daily return data from yahoo using ticker, start date and end date
def retrieve_yahoo_data_volume(ticker = 'spy', start_date = start_data_date, end_date = end_data_date):
    try:
        # get data based on ticker
        yahoo_data = yf.Ticker(ticker)
        print(f"Processing Ticker {ticker}")
        # select data using start date and end data and calculate the daily return
        price_df = yahoo_data.history(start=start_date, end=end_date).Volume
        price_df.name = ticker
        # if no data retrieved raise exception
        if price_df.shape[0] == 0:
            raise Exception("No Prices.")
        return price_df
    # handle exception
    except Exception as ex:
        print(f"Sorry, Data not available for '{ticker}': Exception is {ex}")

In [402]:
# Define function to retrieve ticker daily return data from yahoo using ticker, start date and end date
def retrieve_yahoo_put_options_volume(ticker = 'spy', date = '2007-07-01'):
    try:
        # get data based on ticker
        yahoo_data = yf.Ticker(ticker)
        print(f"Processing Ticker {ticker}")
        # select data using start date and end data and calculate the daily return
        opts = yahoo_data.option_chain()
        price_df = opts.puts
        price_df.name = ticker
        price_df = price_df.volume
        # if no data retrieved raise exception
        if price_df.shape[0] == 0:
            raise Exception("No Prices.")
        return price_df
    # handle exception
    except Exception as ex:
        print(f"Sorry, Data not available for '{ticker}': Exception is {ex}")

In [403]:
# Define function to retrieve ticker daily close data from yahoo using ticker, start date and end date
def retrieve_yahoo_data(ticker = 'spy', start_date = start_data_date, end_date = end_data_date):
    try:
        # get data based on ticker
        yahoo_data = yf.Ticker(ticker)
        print(f"Processing Ticker {ticker}")
        # select data using start date and end data and save the Close data
        price_df = yahoo_data.history(start=start_date, end=end_date)
        price_df.name = ticker
        # if no data retrieved raise exception
        if price_df.shape[0] == 0:
            raise Exception("No Prices.")
        return price_df
    # handle exception
    except Exception as ex:
        print(f"Sorry, Data not available for '{ticker}': Exception is {ex}")

In [404]:
# Set up the variable related to tickers and tickers data
ticker_data_dict = {}
ticker_list = ["^VIX", "spy"]

# Retrieve Tickers
def retrieve_tickers(ticker_data_dict, ticker_list):
    for ticker in ticker_list:
        ticker_data = retrieve_yahoo_data_return(ticker)
        ticker_data_dict[ticker] = ticker_data
        
    return ticker_data_dict
        
ticker_data_dict = retrieve_tickers(ticker_data_dict, ticker_list)
ticker_data_df = pd.DataFrame(ticker_data_dict)
# ticker_data_df = ticker_data_df.dropna()
# Display the ticker data related data frame
ticker_data_df
display(ticker_data_df.shape)

Processing Ticker ^VIX
Processing Ticker spy


(4217, 2)

In [405]:
# check the correlation between various tickers
ticker_data_df.corr()

^VIX       spy
^VIX  1.000000 -0.723776
spy  -0.723776  1.000000

In [406]:
# Plot the cum prod spy and VIX
(1+ticker_data_df[["^VIX", "spy"]]).cumprod().hvplot()

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [407]:
# Get the spy close data and plot it 
spy_close_data = retrieve_yahoo_data_close("spy")
spy_close_dict = {}
spy_close_dict["close"] = spy_close_data
spy_close_df = pd.DataFrame(spy_close_dict)

# Plot the DataFrame with hvplot
spy_close_df.hvplot()

Processing Ticker spy


:Curve   [Date]   (close)

In [408]:
#spy_close_df["close"]
spy_close_df['sma 120'] = spy_close_df["close"].rolling(window=window).mean()
spy_close_df.hvplot()

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [409]:
# Define the two technical indicators - simple moving averages 50 day and 200 day - on the spy close and plot them 
spy_close_df['sma 50'] = spy_close_df["close"].rolling(window=50).mean()
spy_close_df['sma 200'] = spy_close_df["close"].rolling(window=200).mean()
spy_close_df[['sma 50', 'sma 200', "close"]].hvplot()

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [410]:
# Retrieve the vix close data and plot it.
vix_close_data = retrieve_yahoo_data_close("^VIX")
vix_close_dict = {}
vix_close_dict["close"] = vix_close_data
vix_close_df = pd.DataFrame(vix_close_dict)

# Plot the DataFrame with hvplot
vix_close_df.hvplot()

Processing Ticker ^VIX


:Curve   [Date]   (close)

In [411]:
# figure the simple moving average with a 120 day window and plot it.
vix_close_df['sma 120'] = vix_close_df["close"].rolling(window=120).mean()
vix_close_df.hvplot()

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [412]:
# figure out the simple moving average with 20, 50 and 200 day on vix and plot the 50 day moving average against vix close
vix_close_df['sma 20'] = vix_close_df["close"].rolling(window=20).mean()
vix_close_df['sma 50'] = vix_close_df["close"].rolling(window=50).mean()
vix_close_df['sma 200'] = vix_close_df["close"].rolling(window=200).mean()
vix_close_df[['sma 50', "close"]].hvplot(width=1000, height=500)
# Long vix when the vix is above its 50 day Moving Average and short vix when it is below its 50 days Moving Average

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [413]:
# Plot the 200 day simple moving on the vix and vix close.
vix_close_df[['sma 200', "close"]].hvplot(width=1000, height=500)
# Long vix when the vix is above its 50 day Moving Average and short vix when it is below its 50 days Moving Average

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [414]:
# Figure out the simple moving average of 100 and 300 days on vix close and plot the sma 100 and close.
vix_close_df['sma 100'] = vix_close_df["close"].rolling(window=100).mean()
vix_close_df['sma 300'] = vix_close_df["close"].rolling(window=300).mean()
vix_close_df[['sma 100', "close"]].hvplot(width=1000, height=500)

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [415]:
# Set the Signal column
vix_close_df["Signal"] = 0.0

# Generate the trading signal 1 or 0,
# where 1 is when the SMA120 is greater than (or crosses over) the SMA200
# where 0 is when the SMA120 is under the SMA200
vix_close_df["Signal"][120:] = np.where(
    vix_close_df["sma 120"][120:] > vix_close_df["sma 200"][120:], 1.0, 0.0
)

# Calculate the points in time at which a position should be taken, 1 or -1
vix_close_df["Entry/Exit"] = vix_close_df["Signal"].diff()

# Review the DataFrame
vix_close_df

close    sma 120   sma 20   sma 50   sma 200  sma 100  \
Date                                                                    
2005-01-03  14.080000        NaN      NaN      NaN       NaN      NaN   
2005-01-04  13.980000        NaN      NaN      NaN       NaN      NaN   
2005-01-05  14.090000        NaN      NaN      NaN       NaN      NaN   
2005-01-06  13.580000        NaN      NaN      NaN       NaN      NaN   
2005-01-07  13.490000        NaN      NaN      NaN       NaN      NaN   
...               ...        ...      ...      ...       ...      ...   
2021-09-27  18.760000  18.041917  19.0020  18.3620  19.97435  18.1287   
2021-09-28  23.250000  18.094417  19.3550  18.3770  19.97800  18.1773   
2021-09-29  22.559999  18.143333  19.6590  18.4336  19.97425  18.2360   
2021-09-30  23.139999  18.195250  20.0105  18.5382  19.96635  18.2708   
2021-10-01  21.100000  18.232333  20.2450  18.6064  19.95740  18.2634   

              sma 300  Signal  Entry/Exit  
Date                                       
2005-01-03        NaN     0.0         NaN  
2005-01-04        NaN     0.0         0.0  
2005-01-05        NaN     0.0         0.0  
2005-01-06        NaN     0.0         0.0  
2005-01-07        NaN     0.0         0.0  
...               ...     ...         ...  
2021-09-27  21.921833     0.0         0.0  
2021-09-28  21.916533     0.0         0.0  
2021-09-29  21.910667     0.0         0.0  
2021-09-30  21.900867     0.0         0.0  
2021-10-01  21.885067     0.0         0.0  

[4217 rows x 9 columns]

In [416]:
# Visualize entry position relative to close price
entry = vix_close_df[vix_close_df["Entry/Exit"] == 1.0]["close"].hvplot.scatter(
    color='purple',
    marker='^',
    size=200,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize exit position relative to close price
exit = vix_close_df[vix_close_df["Entry/Exit"] == -1.0]["close"].hvplot.scatter(
    color='orange',
    marker='v',
    size=200,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize close price for the investment
security_close = vix_close_df[["close"]].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize moving averages
moving_avgs = vix_close_df[["sma 120", "sma 200"]].hvplot(
    ylabel='Price in $',
    width=1000,
    height=400
)

# Overlay plots
entry_exit_plot = security_close * moving_avgs * entry * exit
entry_exit_plot

:Overlay
   .Curve.I          :Curve   [Date]   (close)
   .NdOverlay.I      :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.Close.I  :Scatter   [Date]   (close)
   .Scatter.Close.II :Scatter   [Date]   (close)

In [417]:
# Set up the technical variable dataframe.
# Figure out the vix return, vix mean, and 10, 15, 20, 50, 100, 150, 200 & 250 day simple moving averages.
# Plot the technical variables
technical_variables_dict = {}
technical_variables_dict["vix close"] = vix_close_data
technical_variables_df = pd.DataFrame(technical_variables_dict)

technical_variables_df["vix return"] = technical_variables_df["vix close"].pct_change()
technical_variables_df["mean"] =technical_variables_df["vix close"].mean()
technical_variables_df['sma 10'] = technical_variables_df["vix close"].rolling(window=10).mean()
technical_variables_df['sma 15'] = technical_variables_df["vix close"].rolling(window=15).mean()
technical_variables_df['sma 20'] = technical_variables_df["vix close"].rolling(window=20).mean()
technical_variables_df['sma 50'] = technical_variables_df["vix close"].rolling(window=50).mean()
technical_variables_df['sma 100'] = technical_variables_df["vix close"].rolling(window=100).mean()
technical_variables_df['sma 150'] = technical_variables_df["vix close"].rolling(window=150).mean()
technical_variables_df['sma 200'] = technical_variables_df["vix close"].rolling(window=200).mean()
technical_variables_df['sma 250'] = technical_variables_df["vix close"].rolling(window=250).mean()

technical_variables_df.hvplot(width=1000, height=500)

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [418]:
# Check if the technical variables have Nan or infinite.
# Make sure everything is finite in the technicalvariables.
display(np.all(np.isfinite(technical_variables_df)))

False

In [419]:
# Set the Signal column with various signals related to above the moving average and below the moving average signals.
technical_variables_df["a15"] = 0.0
technical_variables_df["a50"] = 0.0
technical_variables_df["a100"] = 0.0
technical_variables_df["a150"] = 0.0
technical_variables_df["a200"] = 0.0
technical_variables_df["b15"] = 0.0
technical_variables_df["b50"] = 0.0
technical_variables_df["b100"] = 0.0
technical_variables_df["b150"] = 0.0
technical_variables_df["b200"] = 0.0
technical_variables_df["vix_pos_return"] = 0.0
technical_variables_df["vix_neg_return"] = 0.0

# Generate the trading signal 1 or 0 for various signals
# where 1 is when the vix close is above or below the simple moving averages.
# where 0 is when the simple moving average is under/over the vix close
technical_variables_df["a15"] = np.where(
    technical_variables_df["vix close"] > technical_variables_df["sma 15"], 1.0, 0.0
)
technical_variables_df["a50"] = np.where(
    technical_variables_df["vix close"] > technical_variables_df["sma 50"], 1.0, 0.0
)
technical_variables_df["a100"] = np.where(
    technical_variables_df["vix close"] > technical_variables_df["sma 100"], 1.0, 0.0
)
technical_variables_df["a150"] = np.where(
    technical_variables_df["vix close"] > technical_variables_df["sma 150"], 1.0, 0.0
)
technical_variables_df["a200"] = np.where(
    technical_variables_df["vix close"] > technical_variables_df["sma 200"], 1.0, 0.0
)
technical_variables_df["b15"] = np.where(
    technical_variables_df["sma 15"] > technical_variables_df["vix close"], 1.0, 0.0
)
technical_variables_df["b50"] = np.where(
    technical_variables_df["sma 50"] > technical_variables_df["vix close"], 1.0, 0.0
)
technical_variables_df["b100"] = np.where(
    technical_variables_df["sma 100"] > technical_variables_df["vix close"], 1.0, 0.0
)
technical_variables_df["b150"] = np.where(
    technical_variables_df["sma 150"] > technical_variables_df["vix close"], 1.0, 0.0
)
technical_variables_df["b200"] = np.where(
    technical_variables_df["sma 200"] > technical_variables_df["vix close"], 1.0, 0.0
)
# Create columnes for positive and negative returns
technical_variables_df["vix_pos_return"] = np.where(
    technical_variables_df["vix return"] > 0, 1.0, 0.0
) 
technical_variables_df["vix_neg_return"] = np.where(
    technical_variables_df["vix return"] < 0, 1.0, 0.0
)
# Check the data frame.
technical_variables_df

vix close  vix return       mean  sma 10     sma 15   sma 20  \
Date                                                                       
2005-01-03  14.080000         NaN  19.114446     NaN        NaN      NaN   
2005-01-04  13.980000   -0.007102  19.114446     NaN        NaN      NaN   
2005-01-05  14.090000    0.007868  19.114446     NaN        NaN      NaN   
2005-01-06  13.580000   -0.036196  19.114446     NaN        NaN      NaN   
2005-01-07  13.490000   -0.006627  19.114446     NaN        NaN      NaN   
...               ...         ...        ...     ...        ...      ...   
2021-09-27  18.760000    0.056901  19.114446  20.322  19.896000  19.0020   
2021-09-28  23.250000    0.239339  19.114446  20.701  20.236667  19.3550   
2021-09-29  22.559999   -0.029677  19.114446  21.139  20.543333  19.6590   
2021-09-30  23.139999    0.025709  19.114446  21.584  20.832667  20.0105   
2021-10-01  21.100000   -0.088159  19.114446  21.613  20.842667  20.2450   

             sma 50  sma 100    sma 150   sma 200  ...  a100  a150  a200  b15  \
Date                                               ...                          
2005-01-03      NaN      NaN        NaN       NaN  ...   0.0   0.0   0.0  0.0   
2005-01-04      NaN      NaN        NaN       NaN  ...   0.0   0.0   0.0  0.0   
2005-01-05      NaN      NaN        NaN       NaN  ...   0.0   0.0   0.0  0.0   
2005-01-06      NaN      NaN        NaN       NaN  ...   0.0   0.0   0.0  0.0   
2005-01-07      NaN      NaN        NaN       NaN  ...   0.0   0.0   0.0  0.0   
...             ...      ...        ...       ...  ...   ...   ...   ...  ...   
2021-09-27  18.3620  18.1287  18.774133  19.97435  ...   1.0   0.0   0.0  1.0   
2021-09-28  18.3770  18.1773  18.786867  19.97800  ...   1.0   1.0   1.0  0.0   
2021-09-29  18.4336  18.2360  18.744667  19.97425  ...   1.0   1.0   1.0  0.0   
2021-09-30  18.5382  18.2708  18.712600  19.96635  ...   1.0   1.0   1.0  0.0   
2021-10-01  18.6064  18.2634  18.697600  19.95740  ...   1.0   1.0   1.0  0.0   

            b50  b100  b150  b200  vix_pos_return  vix_neg_return  
Date                                                               
2005-01-03  0.0   0.0   0.0   0.0             0.0             0.0  
2005-01-04  0.0   0.0   0.0   0.0             0.0             1.0  
2005-01-05  0.0   0.0   0.0   0.0             1.0             0.0  
2005-01-06  0.0   0.0   0.0   0.0             0.0             1.0  
2005-01-07  0.0   0.0   0.0   0.0             0.0             1.0  
...         ...   ...   ...   ...             ...             ...  
2021-09-27  0.0   0.0   1.0   1.0             1.0             0.0  
2021-09-28  0.0   0.0   0.0   0.0             1.0             0.0  
2021-09-29  0.0   0.0   0.0   0.0             0.0             1.0  
2021-09-30  0.0   0.0   0.0   0.0             1.0             0.0  
2021-10-01  0.0   0.0   0.0   0.0             0.0             1.0  

[4217 rows x 23 columns]

In [420]:
# Check if the technical variables have Nan or infinite.
# Make sure everything is finite in the technical variables.
display(np.all(np.isfinite(technical_variables_df)))

False

In [421]:
# Create new columns to records cumulative count of 1s. for various signals 
technical_variables_df["c_1_15"] = np.where(
        technical_variables_df["a15"].eq(1),
        technical_variables_df.groupby(technical_variables_df.a15.ne(technical_variables_df.a15.shift()).cumsum()).cumcount() + 1,
        0,
)
technical_variables_df["c_1_50"] = np.where(
        technical_variables_df["a50"].eq(1),
        technical_variables_df.groupby(technical_variables_df.a50.ne(technical_variables_df.a50.shift()).cumsum()).cumcount() + 1,
        0,
)
technical_variables_df["c_1_100"] = np.where(
        technical_variables_df["a100"].eq(1),
        technical_variables_df.groupby(technical_variables_df.a100.ne(technical_variables_df.a100.shift()).cumsum()).cumcount() + 1,
        0,
)
technical_variables_df["c_1_150"] = np.where(
        technical_variables_df["a150"].eq(1),
        technical_variables_df.groupby(technical_variables_df.a150.ne(technical_variables_df.a150.shift()).cumsum()).cumcount() + 1,
        0,
)
technical_variables_df["c_1_200"] = np.where(
        technical_variables_df["a200"].eq(1),
        technical_variables_df.groupby(technical_variables_df.a200.ne(technical_variables_df.a200.shift()).cumsum()).cumcount() + 1,
        0,
)
technical_variables_df["c_pos_returns"] = np.where(
        technical_variables_df["vix_pos_return"].eq(1),
        technical_variables_df.groupby(technical_variables_df.vix_pos_return.ne(technical_variables_df.vix_pos_return.shift()).cumsum()).cumcount() + 1,
        0,
)
technical_variables_df["c_neg_returns"] = np.where(
        technical_variables_df["vix_neg_return"].eq(1),
        technical_variables_df.groupby(technical_variables_df.vix_neg_return.ne(technical_variables_df.vix_neg_return.shift()).cumsum()).cumcount() + 1,
        0,
)

# display the new technical variables dataframe.
technical_variables_df

vix close  vix return       mean  sma 10     sma 15   sma 20  \
Date                                                                       
2005-01-03  14.080000         NaN  19.114446     NaN        NaN      NaN   
2005-01-04  13.980000   -0.007102  19.114446     NaN        NaN      NaN   
2005-01-05  14.090000    0.007868  19.114446     NaN        NaN      NaN   
2005-01-06  13.580000   -0.036196  19.114446     NaN        NaN      NaN   
2005-01-07  13.490000   -0.006627  19.114446     NaN        NaN      NaN   
...               ...         ...        ...     ...        ...      ...   
2021-09-27  18.760000    0.056901  19.114446  20.322  19.896000  19.0020   
2021-09-28  23.250000    0.239339  19.114446  20.701  20.236667  19.3550   
2021-09-29  22.559999   -0.029677  19.114446  21.139  20.543333  19.6590   
2021-09-30  23.139999    0.025709  19.114446  21.584  20.832667  20.0105   
2021-10-01  21.100000   -0.088159  19.114446  21.613  20.842667  20.2450   

             sma 50  sma 100    sma 150   sma 200  ...  b200  vix_pos_return  \
Date                                               ...                         
2005-01-03      NaN      NaN        NaN       NaN  ...   0.0             0.0   
2005-01-04      NaN      NaN        NaN       NaN  ...   0.0             0.0   
2005-01-05      NaN      NaN        NaN       NaN  ...   0.0             1.0   
2005-01-06      NaN      NaN        NaN       NaN  ...   0.0             0.0   
2005-01-07      NaN      NaN        NaN       NaN  ...   0.0             0.0   
...             ...      ...        ...       ...  ...   ...             ...   
2021-09-27  18.3620  18.1287  18.774133  19.97435  ...   1.0             1.0   
2021-09-28  18.3770  18.1773  18.786867  19.97800  ...   0.0             1.0   
2021-09-29  18.4336  18.2360  18.744667  19.97425  ...   0.0             0.0   
2021-09-30  18.5382  18.2708  18.712600  19.96635  ...   0.0             1.0   
2021-10-01  18.6064  18.2634  18.697600  19.95740  ...   0.0             0.0   

            vix_neg_return  c_1_15  c_1_50  c_1_100  c_1_150  c_1_200  \
Date                                                                    
2005-01-03             0.0       0       0        0        0        0   
2005-01-04             1.0       0       0        0        0        0   
2005-01-05             0.0       0       0        0        0        0   
2005-01-06             1.0       0       0        0        0        0   
2005-01-07             1.0       0       0        0        0        0   
...                    ...     ...     ...      ...      ...      ...   
2021-09-27             0.0       0       1        1        0        0   
2021-09-28             0.0       1       2        2        1        1   
2021-09-29             1.0       2       3        3        2        2   
2021-09-30             0.0       3       4        4        3        3   
2021-10-01             1.0       4       5        5        4        4   

            c_pos_returns  c_neg_returns  
Date                                      
2005-01-03              0              0  
2005-01-04              0              1  
2005-01-05              1              0  
2005-01-06              0              1  
2005-01-07              0              2  
...                   ...            ...  
2021-09-27              1              0  
2021-09-28              2              0  
2021-09-29              0              1  
2021-09-30              1              0  
2021-10-01              0              1  

[4217 rows x 30 columns]

In [422]:
# Check if the technical variables have Nan or infinite.
# Make sure everything is finite in the technicalvariables.
display(np.all(np.isfinite(technical_variables_df)))

False

In [423]:
# Create new columns related to more than or equal to 3 consecutive 1 signals.
technical_variables_df["c_3_15"] = np.where(technical_variables_df["c_1_15"] >= 3, 1, 0)
technical_variables_df["c_3_50"] = np.where(technical_variables_df["c_1_50"] >= 3, 1, 0)
technical_variables_df["c_3_100"] = np.where(technical_variables_df["c_1_100"] >= 3, 1, 0)
technical_variables_df["c_3_150"] = np.where(technical_variables_df["c_1_150"] >= 3, 1, 0)
technical_variables_df["c_3_200"] = np.where(technical_variables_df["c_1_200"] >= 3, 1, 0)
technical_variables_df["c_3_pos_returns"] = np.where(technical_variables_df["c_pos_returns"] >= 3, 1, 0)
technical_variables_df["c_3_neg_returns"] = np.where(technical_variables_df["c_neg_returns"] >= 3, 1, 0)
technical_variables_df

vix close  vix return       mean  sma 10     sma 15   sma 20  \
Date                                                                       
2005-01-03  14.080000         NaN  19.114446     NaN        NaN      NaN   
2005-01-04  13.980000   -0.007102  19.114446     NaN        NaN      NaN   
2005-01-05  14.090000    0.007868  19.114446     NaN        NaN      NaN   
2005-01-06  13.580000   -0.036196  19.114446     NaN        NaN      NaN   
2005-01-07  13.490000   -0.006627  19.114446     NaN        NaN      NaN   
...               ...         ...        ...     ...        ...      ...   
2021-09-27  18.760000    0.056901  19.114446  20.322  19.896000  19.0020   
2021-09-28  23.250000    0.239339  19.114446  20.701  20.236667  19.3550   
2021-09-29  22.559999   -0.029677  19.114446  21.139  20.543333  19.6590   
2021-09-30  23.139999    0.025709  19.114446  21.584  20.832667  20.0105   
2021-10-01  21.100000   -0.088159  19.114446  21.613  20.842667  20.2450   

             sma 50  sma 100    sma 150   sma 200  ...  c_1_200  \
Date                                               ...            
2005-01-03      NaN      NaN        NaN       NaN  ...        0   
2005-01-04      NaN      NaN        NaN       NaN  ...        0   
2005-01-05      NaN      NaN        NaN       NaN  ...        0   
2005-01-06      NaN      NaN        NaN       NaN  ...        0   
2005-01-07      NaN      NaN        NaN       NaN  ...        0   
...             ...      ...        ...       ...  ...      ...   
2021-09-27  18.3620  18.1287  18.774133  19.97435  ...        0   
2021-09-28  18.3770  18.1773  18.786867  19.97800  ...        1   
2021-09-29  18.4336  18.2360  18.744667  19.97425  ...        2   
2021-09-30  18.5382  18.2708  18.712600  19.96635  ...        3   
2021-10-01  18.6064  18.2634  18.697600  19.95740  ...        4   

            c_pos_returns  c_neg_returns  c_3_15  c_3_50  c_3_100  c_3_150  \
Date                                                                         
2005-01-03              0              0       0       0        0        0   
2005-01-04              0              1       0       0        0        0   
2005-01-05              1              0       0       0        0        0   
2005-01-06              0              1       0       0        0        0   
2005-01-07              0              2       0       0        0        0   
...                   ...            ...     ...     ...      ...      ...   
2021-09-27              1              0       0       0        0        0   
2021-09-28              2              0       0       0        0        0   
2021-09-29              0              1       0       1        1        0   
2021-09-30              1              0       1       1        1        1   
2021-10-01              0              1       1       1        1        1   

            c_3_200  c_3_pos_returns  c_3_neg_returns  
Date                                                   
2005-01-03        0                0                0  
2005-01-04        0                0                0  
2005-01-05        0                0                0  
2005-01-06        0                0                0  
2005-01-07        0                0                0  
...             ...              ...              ...  
2021-09-27        0                0                0  
2021-09-28        0                0                0  
2021-09-29        0                0                0  
2021-09-30        1                0                0  
2021-10-01        1                0                0  

[4217 rows x 37 columns]

In [424]:
# Check if the technical variables have Nan or infinite.
# Make sure everything is finite in the technical variables.
display(np.all(np.isfinite(technical_variables_df)))

False

In [425]:
# Check the balance among the 3 or more consecutive 1s for positive and negative returns.
display(technical_variables_df["c_3_pos_returns"].value_counts())
display(technical_variables_df["c_3_neg_returns"].value_counts())

0    3882
1     335
Name: c_3_pos_returns, dtype: int64

0    3606
1     611
Name: c_3_neg_returns, dtype: int64

In [426]:
# Visualize entry position relative to close price
entry_3_100_day = technical_variables_df[(technical_variables_df["c_3_100"] == 1.0) & (technical_variables_df["c_3_15"] == 1.0) & (technical_variables_df["c_3_50"] == 1.0)]["vix close"].hvplot.scatter(
    color='purple',
    marker='^',
    size=20,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

'''
# Visualize exit position relative to close price
exit = vix_close_df[vix_close_df["Entry/Exit"] == -1.0]["close"].hvplot.scatter(
    color='orange',
    marker='v',
    size=200,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)
'''

# Visualize close price for the investment
security_3_100_close = technical_variables_df[["vix close"]].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize moving averages
moving_avgs_14_50_100 = technical_variables_df[["sma 50"]].hvplot(
    ylabel='Price in $',
    width=1000,
    height=400
)

# Overlay plots
entry_exit_3_100_plot = security_3_100_close * moving_avgs_14_50_100 * entry_3_100_day
entry_exit_3_100_plot

:Overlay
   .Curve.I           :Curve   [Date]   (vix close)
   .Curve.II          :Curve   [Date]   (sma 50)
   .Scatter.Vix_close :Scatter   [Date]   (vix close)

In [427]:
# Visualize entry position relative to close price
entry_3_pos_returns_day = technical_variables_df[(technical_variables_df["c_3_pos_returns"] == 1.0)]["vix close"].hvplot.scatter(
    color='purple',
    marker='^',
    size=20,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize exit position relative to close price
exit_3_neg_returns_day = technical_variables_df[technical_variables_df["c_3_neg_returns"] == 1.0]["vix close"].hvplot.scatter(
    color='orange',
    marker='v',
    size=20,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize close price for the investment
security_3_close = technical_variables_df[["vix close"]].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize moving averages
#moving_avgs_14_50_100 = technical_variables_df[["sma 50"]].hvplot(
#    ylabel='Price in $',
#    width=1000,
#    height=400
#)

# Overlay plots
entry_exit_3_returns_plot = security_3_close * entry_3_pos_returns_day * exit_3_neg_returns_day
entry_exit_3_returns_plot

:Overlay
   .Curve.I              :Curve   [Date]   (vix close)
   .Scatter.Vix_close.I  :Scatter   [Date]   (vix close)
   .Scatter.Vix_close.II :Scatter   [Date]   (vix close)

In [428]:
# Visualize entry position relative to close price
entry_strategy_day = technical_variables_df[(technical_variables_df["c_3_100"] == 1.0) & (technical_variables_df["c_3_15"] == 1.0) & (technical_variables_df["c_3_50"] == 1.0)]["vix close"].hvplot.scatter(
    color='purple',
    marker='^',
    size=20,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize exit position relative to close price
exit_strategy_day = technical_variables_df[technical_variables_df["c_3_neg_returns"] == 1.0]["vix close"].hvplot.scatter(
    color='orange',
    marker='v',
    size=20,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize close price for the investment
security_3_close = technical_variables_df[["vix close"]].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize moving averages
#moving_avgs_14_50_100 = technical_variables_df[["sma 50"]].hvplot(
#    ylabel='Price in $',
#    width=1000,
#    height=400
#)

# Overlay plots
entry_exit_3_returns_plot = security_3_close * entry_strategy_day * exit_strategy_day
entry_exit_3_returns_plot

:Overlay
   .Curve.I              :Curve   [Date]   (vix close)
   .Scatter.Vix_close.I  :Scatter   [Date]   (vix close)
   .Scatter.Vix_close.II :Scatter   [Date]   (vix close)

In [429]:
# Create a new data frame to track the bollinger bands and plot the columns
vix_df = retrieve_yahoo_data("^VIX")
# vix_dict = {}
#vix_dict["close"] = vix_close_data
#vix_close_df = pd.DataFrame(vix_close_dict)
vix_df = vix_df .drop(columns=["Dividends", "Stock Splits"])
vix_df.columns=["open", "high", "low", "close", "volume"]


# Plot the DataFrame with hvplot
# vix_close_df.hvplot()
# Determine the Bollinger Bands for the Dataset
bbands_vix_df = TA.BBANDS(vix_df)
vix_df = pd.concat([vix_df, bbands_vix_df], axis=1)
vix_df[["close", "BB_UPPER", "BB_LOWER"]].hvplot()

Processing Ticker ^VIX


:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [430]:
# Create new columns related to when VIX Close is greater than BB UPPER and VIX Close is smaller than BB LOWER
vix_df[">b_upper"] = np.where(vix_df["close"] >= vix_df["BB_UPPER"], 1, 0)
vix_df["<b_lower"] = np.where(vix_df["BB_LOWER"] >= vix_df["close"], 1, 0)
print(vix_df[">b_upper"].value_counts())
print(vix_df["<b_lower"].value_counts())

0    3932
1     285
Name: >b_upper, dtype: int64
0    4167
1      50
Name: <b_lower, dtype: int64


In [431]:
# Check if the technical variables have Nan or infinite.
# Make sure everything is finite in the technical variables.
display(np.all(np.isfinite(vix_df)))

False

In [432]:
# Visualize entry position relative to close price
entry_vix = vix_df[vix_df[">b_upper"] == 1.0]["close"].hvplot.scatter(
    color='purple',
    marker='^',
    size=200,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize exit position relative to close price
exit_vix = vix_df[vix_df["<b_lower"] == 1.0]["close"].hvplot.scatter(
    color='orange',
    marker='v',
    size=200,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize close price for the investment
security_close_vix = vix_df[["close"]].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize moving averages
bollinger_band_vix = vix_df[["BB_UPPER", "BB_LOWER"]].hvplot(
    ylabel='Price in $',
    width=1000,
    height=400
)

# Overlay plots
entry_exit_vix_plot = security_close_vix * bollinger_band_vix * entry_vix * exit_vix
entry_exit_vix_plot

:Overlay
   .Curve.I          :Curve   [Date]   (close)
   .NdOverlay.I      :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.Close.I  :Scatter   [Date]   (close)
   .Scatter.Close.II :Scatter   [Date]   (close)

In [433]:
# Copy the columns to the technical variables data frame from vix dataframe and check the updated dataframe.
technical_variables_df[">b_upper"] = vix_df[">b_upper"]
technical_variables_df["<b_lower"] = vix_df["<b_lower"]
technical_variables_df

vix close  vix return       mean  sma 10     sma 15   sma 20  \
Date                                                                       
2005-01-03  14.080000         NaN  19.114446     NaN        NaN      NaN   
2005-01-04  13.980000   -0.007102  19.114446     NaN        NaN      NaN   
2005-01-05  14.090000    0.007868  19.114446     NaN        NaN      NaN   
2005-01-06  13.580000   -0.036196  19.114446     NaN        NaN      NaN   
2005-01-07  13.490000   -0.006627  19.114446     NaN        NaN      NaN   
...               ...         ...        ...     ...        ...      ...   
2021-09-27  18.760000    0.056901  19.114446  20.322  19.896000  19.0020   
2021-09-28  23.250000    0.239339  19.114446  20.701  20.236667  19.3550   
2021-09-29  22.559999   -0.029677  19.114446  21.139  20.543333  19.6590   
2021-09-30  23.139999    0.025709  19.114446  21.584  20.832667  20.0105   
2021-10-01  21.100000   -0.088159  19.114446  21.613  20.842667  20.2450   

             sma 50  sma 100    sma 150   sma 200  ...  c_neg_returns  c_3_15  \
Date                                               ...                          
2005-01-03      NaN      NaN        NaN       NaN  ...              0       0   
2005-01-04      NaN      NaN        NaN       NaN  ...              1       0   
2005-01-05      NaN      NaN        NaN       NaN  ...              0       0   
2005-01-06      NaN      NaN        NaN       NaN  ...              1       0   
2005-01-07      NaN      NaN        NaN       NaN  ...              2       0   
...             ...      ...        ...       ...  ...            ...     ...   
2021-09-27  18.3620  18.1287  18.774133  19.97435  ...              0       0   
2021-09-28  18.3770  18.1773  18.786867  19.97800  ...              0       0   
2021-09-29  18.4336  18.2360  18.744667  19.97425  ...              1       0   
2021-09-30  18.5382  18.2708  18.712600  19.96635  ...              0       1   
2021-10-01  18.6064  18.2634  18.697600  19.95740  ...              1       1   

            c_3_50  c_3_100  c_3_150  c_3_200  c_3_pos_returns  \
Date                                                             
2005-01-03       0        0        0        0                0   
2005-01-04       0        0        0        0                0   
2005-01-05       0        0        0        0                0   
2005-01-06       0        0        0        0                0   
2005-01-07       0        0        0        0                0   
...            ...      ...      ...      ...              ...   
2021-09-27       0        0        0        0                0   
2021-09-28       0        0        0        0                0   
2021-09-29       1        1        0        0                0   
2021-09-30       1        1        1        1                0   
2021-10-01       1        1        1        1                0   

            c_3_neg_returns  >b_upper  <b_lower  
Date                                             
2005-01-03                0         0         0  
2005-01-04                0         0         0  
2005-01-05                0         0         0  
2005-01-06                0         0         0  
2005-01-07                0         0         0  
...                     ...       ...       ...  
2021-09-27                0         0         0  
2021-09-28                0         0         0  
2021-09-29                0         0         0  
2021-09-30                0         0         0  
2021-10-01                0         0         0  

[4217 rows x 39 columns]

In [434]:
# Check if the data is finite or has nans, etc.
display(np.all(np.isfinite(technical_variables_df)))

False

In [435]:
# Save the technical indicators to the csv file.
technical_variables_date_df = technical_variables_df.reset_index()
technical_variables_date_df.to_csv('technical_indicators.csv', index=False) 
technical_variables_date_df.head(5)
technical_variables_date_df.tail(5)

Date  vix close  vix return       mean  sma 10     sma 15   sma 20  \
4212 2021-09-27  18.760000    0.056901  19.114446  20.322  19.896000  19.0020   
4213 2021-09-28  23.250000    0.239339  19.114446  20.701  20.236667  19.3550   
4214 2021-09-29  22.559999   -0.029677  19.114446  21.139  20.543333  19.6590   
4215 2021-09-30  23.139999    0.025709  19.114446  21.584  20.832667  20.0105   
4216 2021-10-01  21.100000   -0.088159  19.114446  21.613  20.842667  20.2450   

       sma 50  sma 100    sma 150  ...  c_neg_returns  c_3_15  c_3_50  \
4212  18.3620  18.1287  18.774133  ...              0       0       0   
4213  18.3770  18.1773  18.786867  ...              0       0       0   
4214  18.4336  18.2360  18.744667  ...              1       0       1   
4215  18.5382  18.2708  18.712600  ...              0       1       1   
4216  18.6064  18.2634  18.697600  ...              1       1       1   

      c_3_100  c_3_150  c_3_200  c_3_pos_returns  c_3_neg_returns  >b_upper  \
4212        0        0        0                0                0         0   
4213        0        0        0                0                0         0   
4214        1        0        0                0                0         0   
4215        1        1        1                0                0         0   
4216        1        1        1                0                0         0   

      <b_lower  
4212         0  
4213         0  
4214         0  
4215         0  
4216         0  

[5 rows x 40 columns]

In [436]:
# Check the correlation of various features
technical_variables_df.corr()

vix close  vix return  mean    sma 10    sma 15    sma 20  \
vix close         1.000000    0.109501   NaN  0.960041  0.941760  0.923363   
vix return        0.109501    1.000000   NaN -0.032715 -0.035617 -0.037074   
mean                   NaN         NaN   NaN       NaN       NaN       NaN   
sma 10            0.960041   -0.032715   NaN  1.000000  0.993066  0.980315   
sma 15            0.941760   -0.035617   NaN  0.993066  1.000000  0.994917   
sma 20            0.923363   -0.037074   NaN  0.980315  0.994917  1.000000   
sma 50            0.828870   -0.036398   NaN  0.888430  0.913693  0.935854   
sma 100           0.733867   -0.030691   NaN  0.783000  0.805507  0.826764   
sma 150           0.661892   -0.027406   NaN  0.704457  0.724392  0.743631   
sma 200           0.611658   -0.024473   NaN  0.649612  0.667440  0.684744   
sma 250           0.567533   -0.024392   NaN  0.602931  0.619497  0.635618   
a15               0.148580    0.304863   NaN -0.014794 -0.060786 -0.082204   
a50               0.248252    0.204643   NaN  0.142280  0.098680  0.060959   
a100              0.320323    0.165115   NaN  0.244014  0.211506  0.182665   
a150              0.408688    0.143763   NaN  0.346717  0.320550  0.297470   
a200              0.458326    0.138977   NaN  0.406496  0.384768  0.365538   
b15              -0.144286   -0.304504   NaN  0.016368  0.060786  0.082204   
b50              -0.230283   -0.202252   NaN -0.127384 -0.085597 -0.049634   
b100             -0.286723   -0.161645   NaN -0.213397 -0.182481 -0.155155   
b150             -0.352449   -0.139077   NaN -0.293576 -0.269400 -0.248246   
b200             -0.383274   -0.133993   NaN -0.333379 -0.313153 -0.295393   
vix_pos_return    0.047991    0.681349   NaN -0.041345 -0.042154 -0.042523   
vix_neg_return   -0.043181   -0.680376   NaN  0.045931  0.046660  0.046665   
c_1_15            0.277280    0.098687   NaN  0.146771  0.080805  0.036412   
c_1_50            0.428851    0.007972   NaN  0.401032  0.370613  0.338298   
c_1_100           0.469534   -0.015452   NaN  0.485951  0.478287  0.465166   
c_1_150           0.306900   -0.017106   NaN  0.327228  0.329717  0.328162   
c_1_200           0.441510   -0.013596   NaN  0.464937  0.470653  0.473837   
c_pos_returns     0.047114    0.532772   NaN -0.059014 -0.062045 -0.062476   
c_neg_returns    -0.059794   -0.441692   NaN  0.048621  0.050581  0.051615   
c_3_15            0.171537    0.083184   NaN  0.035588 -0.016887 -0.044758   
c_3_50            0.275832    0.031851   NaN  0.195257  0.149263  0.109163   
c_3_100           0.343661    0.015266   NaN  0.295119  0.261586  0.230457   
c_3_150           0.427092    0.008110   NaN  0.392415  0.366879  0.342986   
c_3_200           0.488473    0.006454   NaN  0.462277  0.440793  0.421306   
c_3_pos_returns   0.021984    0.248765   NaN -0.054931 -0.056928 -0.056607   
c_3_neg_returns  -0.046830   -0.217300   NaN  0.041277  0.042226  0.043278   
>b_upper          0.119070    0.439155   NaN -0.020846 -0.041704 -0.053427   
<b_lower         -0.043656   -0.079807   NaN -0.019454 -0.016612 -0.015386   

                   sma 50   sma 100   sma 150   sma 200  ...  c_neg_returns  \
vix close        0.828870  0.733867  0.661892  0.611658  ...      -0.059794   
vix return      -0.036398 -0.030691 -0.027406 -0.024473  ...      -0.441692   
mean                  NaN       NaN       NaN       NaN  ...            NaN   
sma 10           0.888430  0.783000  0.704457  0.649612  ...       0.048621   
sma 15           0.913693  0.805507  0.724392  0.667440  ...       0.050581   
sma 20           0.935854  0.826764  0.743631  0.684744  ...       0.051615   
sma 50           1.000000  0.928684  0.845375  0.778287  ...       0.050678   
sma 100          0.928684  1.000000  0.957797  0.895753  ...       0.035398   
sma 150          0.845375  0.957797  1.000000  0.971172  ...       0.034667   
sma 200          0.778287  0.895753  0.971172  1.000000  ...       0.037866   
sma 250          0.723867  

In [437]:
# Read the day of the week prophet data from the csv
prophet_df = pd.read_csv("prophet_output_day_of_week.csv")
prophet_df

Date         y  Friday  Monday  Thursday  Tuesday  Wednesday
0     2006-07-03       NaN       0       1         0        0          0
1     2006-07-05  0.084291       0       0         0        0          1
2     2006-07-06 -0.035336       0       0         1        0          0
3     2006-07-07  0.023443       1       0         0        0          0
4     2006-07-10  0.003579       0       1         0        0          0
...          ...       ...     ...     ...       ...      ...        ...
3835  2021-09-27  0.056901       0       1         0        0          0
3836  2021-09-28  0.239339       0       0         0        1          0
3837  2021-09-29 -0.029677       0       0         0        0          1
3838  2021-09-30  0.025709       0       0         1        0          0
3839  2021-10-01 -0.088159       1       0         0        0          0

[3840 rows x 7 columns]

In [438]:
# Set up the temp technical variables
temp_technical_variables_df = technical_variables_df.copy()
temp_technical_variables_df = temp_technical_variables_df.loc["2006-07-03":,:]
temp_prophet_df = prophet_df.copy()
display(temp_technical_variables_df.head(1))
display(temp_technical_variables_df.tail(1))

# Set up the temp prophet data frame
temp_prophet_df = temp_prophet_df.drop(columns=["Date", "y"])
display(temp_prophet_df.head(1))
display(temp_prophet_df.tail(1))
#display(temp_technical_variables_df.head())
#display(temp_prophet_df.head())

# Set up the technical variables by concatenating the temp technical variables and prophet data
technical_variables_enhanced_df = pd.concat([temp_technical_variables_df.reset_index(), temp_prophet_df], axis=1)
technical_variables_enhanced_df = technical_variables_enhanced_df.set_index("Date").dropna()
technical_variables_enhanced_df

vix close  vix return       mean  sma 10  sma 15   sma 20  sma 50  \
Date                                                                            
2006-07-03      13.05   -0.002294  19.114446  15.095   16.48  16.9885  15.239   

            sma 100  sma 150   sma 200  ...  c_neg_returns  c_3_15  c_3_50  \
Date                                    ...                                  
2006-07-03  13.5626  12.9816  13.09455  ...              1       0       0   

            c_3_100  c_3_150  c_3_200  c_3_pos_returns  c_3_neg_returns  \
Date                                                                      
2006-07-03        0        1        0                0                0   

            >b_upper  <b_lower  
Date                            
2006-07-03         0         0  

[1 rows x 39 columns]

vix close  vix return       mean  sma 10     sma 15  sma 20  \
Date                                                                      
2021-10-01       21.1   -0.088159  19.114446  21.613  20.842667  20.245   

             sma 50  sma 100  sma 150  sma 200  ...  c_neg_returns  c_3_15  \
Date                                            ...                          
2021-10-01  18.6064  18.2634  18.6976  19.9574  ...              1       1   

            c_3_50  c_3_100  c_3_150  c_3_200  c_3_pos_returns  \
Date                                                             
2021-10-01       1        1        1        1                0   

            c_3_neg_returns  >b_upper  <b_lower  
Date                                             
2021-10-01                0         0         0  

[1 rows x 39 columns]

Friday  Monday  Thursday  Tuesday  Wednesday
0       0       1         0        0          0

Friday  Monday  Thursday  Tuesday  Wednesday
3839       1       0         0        0          0

vix close  vix return       mean  sma 10     sma 15   sma 20  \
Date                                                                       
2006-07-03  13.050000   -0.002294  19.114446  15.095  16.480000  16.9885   
2006-07-05  14.150000    0.084291  19.114446  14.841  15.836000  16.8290   
2006-07-06  13.650000   -0.035336  19.114446  14.654  15.315333  16.6215   
2006-07-07  13.970000    0.023443  19.114446  14.463  15.186667  16.4025   
2006-07-10  14.020000    0.003579  19.114446  14.276  14.971333  16.1975   
...               ...         ...        ...     ...        ...      ...   
2021-09-27  18.760000    0.056901  19.114446  20.322  19.896000  19.0020   
2021-09-28  23.250000    0.239339  19.114446  20.701  20.236667  19.3550   
2021-09-29  22.559999   -0.029677  19.114446  21.139  20.543333  19.6590   
2021-09-30  23.139999    0.025709  19.114446  21.584  20.832667  20.0105   
2021-10-01  21.100000   -0.088159  19.114446  21.613  20.842667  20.2450   

             sma 50  sma 100    sma 150   sma 200  ...  c_3_200  \
Date                                               ...            
2006-07-03  15.2390  13.5626  12.981600  13.09455  ...        0   
2006-07-05  15.2870  13.5729  12.997000  13.10920  ...        0   
2006-07-06  15.3250  13.5807  13.008733  13.11675  ...        0   
2006-07-07  15.3692  13.5869  13.021467  13.12340  ...        1   
2006-07-10  15.4128  13.6046  13.040000  13.12455  ...        1   
...             ...      ...        ...       ...  ...      ...   
2021-09-27  18.3620  18.1287  18.774133  19.97435  ...        0   
2021-09-28  18.3770  18.1773  18.786867  19.97800  ...        0   
2021-09-29  18.4336  18.2360  18.744667  19.97425  ...        0   
2021-09-30  18.5382  18.2708  18.712600  19.96635  ...        1   
2021-10-01  18.6064  18.2634  18.697600  19.95740  ...        1   

            c_3_pos_returns  c_3_neg_returns  >b_upper  <b_lower  Friday  \
Date                                                                       
2006-07-03                0                0         0         0       0   
2006-07-05                0                0         0         0       0   
2006-07-06                0                0         0         0       0   
2006-07-07                0                0         0         0       1   
2006-07-10                0                0         0         0       0   
...                     ...              ...       ...       ...     ...   
2021-09-27                0                0         0         0       0   
2021-09-28                0                0         0         0       0   
2021-09-29                0                0         0         0       0   
2021-09-30                0                0         0         0       0   
2021-10-01                0                0         0         0       1   

            Monday  Thursday  Tuesday  Wednesday  
Date                                              
2006-07-03       1         0        0          0  
2006-07-05       0         0        0          1  
2006-07-06       0         1        0          0  
2006-07-07       0         0        0          0  
2006-07-10       1         0        0          0  
...            ...       ...      ...        ...  
2021-09-27       1         0        0          0  
2021-09-28       0         0        1          0  
2021-09-29       0         0        0          1  
2021-09-30       0         1        0          0  
2021-10-01       0         0        0          0  

[3840 rows x 44 columns]

In [439]:
# Check if the data is finite or has nans, etc.
display(np.all(np.isfinite(technical_variables_enhanced_df)))
display(np.any(np.isnan(technical_variables_enhanced_df)))
# display(technical_variables_enhanced_df.isna().sum())

True

False

In [440]:
# Initialize the new Signal column
technical_variables_enhanced_df['Signal'] = 0.0

# When Actual Returns are greater than or equal to 0, generate signal to buy stock long
technical_variables_enhanced_df.loc[(technical_variables_enhanced_df['vix return'] >= 0), 'Signal'] = 1

# When Actual Returns are less than 0, generate signal to sell stock short
technical_variables_enhanced_df.loc[(technical_variables_enhanced_df['vix return'] < 0), 'Signal'] = 0

#technical_variables_enhanced_df = technical_variables_enhanced_df.iloc[200:,:]
#technical_variables_enhanced_df = technical_variables_enhanced_df.loc["2007-01-01":,:]

# Review the DataFrame
display(technical_variables_enhanced_df.head())
display(technical_variables_enhanced_df.tail())

vix close  vix return       mean  sma 10     sma 15   sma 20  \
Date                                                                       
2006-07-03      13.05   -0.002294  19.114446  15.095  16.480000  16.9885   
2006-07-05      14.15    0.084291  19.114446  14.841  15.836000  16.8290   
2006-07-06      13.65   -0.035336  19.114446  14.654  15.315333  16.6215   
2006-07-07      13.97    0.023443  19.114446  14.463  15.186667  16.4025   
2006-07-10      14.02    0.003579  19.114446  14.276  14.971333  16.1975   

             sma 50  sma 100    sma 150   sma 200  ...  c_3_pos_returns  \
Date                                               ...                    
2006-07-03  15.2390  13.5626  12.981600  13.09455  ...                0   
2006-07-05  15.2870  13.5729  12.997000  13.10920  ...                0   
2006-07-06  15.3250  13.5807  13.008733  13.11675  ...                0   
2006-07-07  15.3692  13.5869  13.021467  13.12340  ...                0   
2006-07-10  15.4128  13.6046  13.040000  13.12455  ...                0   

            c_3_neg_returns  >b_upper  <b_lower  Friday  Monday  Thursday  \
Date                                                                        
2006-07-03                0         0         0       0       1         0   
2006-07-05                0         0         0       0       0         0   
2006-07-06                0         0         0       0       0         1   
2006-07-07                0         0         0       1       0         0   
2006-07-10                0         0         0       0       1         0   

            Tuesday  Wednesday  Signal  
Date                                    
2006-07-03        0          0     0.0  
2006-07-05        0          1     1.0  
2006-07-06        0          0     0.0  
2006-07-07        0          0     1.0  
2006-07-10        0          0     1.0  

[5 rows x 45 columns]

vix close  vix return       mean  sma 10     sma 15   sma 20  \
Date                                                                       
2021-09-27  18.760000    0.056901  19.114446  20.322  19.896000  19.0020   
2021-09-28  23.250000    0.239339  19.114446  20.701  20.236667  19.3550   
2021-09-29  22.559999   -0.029677  19.114446  21.139  20.543333  19.6590   
2021-09-30  23.139999    0.025709  19.114446  21.584  20.832667  20.0105   
2021-10-01  21.100000   -0.088159  19.114446  21.613  20.842667  20.2450   

             sma 50  sma 100    sma 150   sma 200  ...  c_3_pos_returns  \
Date                                               ...                    
2021-09-27  18.3620  18.1287  18.774133  19.97435  ...                0   
2021-09-28  18.3770  18.1773  18.786867  19.97800  ...                0   
2021-09-29  18.4336  18.2360  18.744667  19.97425  ...                0   
2021-09-30  18.5382  18.2708  18.712600  19.96635  ...                0   
2021-10-01  18.6064  18.2634  18.697600  19.95740  ...                0   

            c_3_neg_returns  >b_upper  <b_lower  Friday  Monday  Thursday  \
Date                                                                        
2021-09-27                0         0         0       0       1         0   
2021-09-28                0         0         0       0       0         0   
2021-09-29                0         0         0       0       0         0   
2021-09-30                0         0         0       0       0         1   
2021-10-01                0         0         0       1       0         0   

            Tuesday  Wednesday  Signal  
Date                                    
2021-09-27        0          0     1.0  
2021-09-28        1          0     1.0  
2021-09-29        0          1     0.0  
2021-09-30        0          0     1.0  
2021-10-01        0          0     0.0  

[5 rows x 45 columns]

In [441]:
# Check the value counts of signal in the dataframe
technical_variables_enhanced_df['Signal'].value_counts()

0.0    2068
1.0    1772
Name: Signal, dtype: int64

In [442]:
# check if the data is finite or has nans, etc.
display(np.all(np.isfinite(technical_variables_enhanced_df)))

True

In [443]:
# Visualize closing price when the signal is 1
signal_1 = technical_variables_enhanced_df[technical_variables_enhanced_df["Signal"] == 1.0]["vix close"].hvplot.scatter(
    color='green',
    marker='^',
    size=10,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize closing price when the signal is -1
signal_neg_1 = technical_variables_enhanced_df[technical_variables_enhanced_df["Signal"] == -1.0]["vix close"].hvplot.scatter(
    color='red',
    marker='v',
    size=10,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize close price for the investment
security_close = technical_variables_enhanced_df[["vix close"]].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400
)
# Visualize moving averages
#moving_avgs = technical_variables_enhanced_df[["SMA_Fast", "SMA_Slow"]].hvplot(
#    ylabel='Price in $',
#    width=1000,
#    height=400
#)

# Overlay plots
entry_exit_plot = security_close *  signal_1 * signal_neg_1 # moving_avgs
entry_exit_plot

:Overlay
   .Curve.I              :Curve   [Date]   (vix close)
   .Scatter.Vix_close.I  :Scatter   [Date]   (vix close)
   .Scatter.Vix_close.II :Scatter   [Date]   (vix close)

In [444]:
# Calculate the strategy returns and add them to the signals_df DataFrame
# NOTE that the signal is from the previous period.
technical_variables_enhanced_df['Strategy Returns'] = technical_variables_enhanced_df['vix return'] * technical_variables_enhanced_df['Signal'].shift()

# Review the DataFrame
display(technical_variables_enhanced_df.head())
display(technical_variables_enhanced_df.tail())

vix close  vix return       mean  sma 10     sma 15   sma 20  \
Date                                                                       
2006-07-03      13.05   -0.002294  19.114446  15.095  16.480000  16.9885   
2006-07-05      14.15    0.084291  19.114446  14.841  15.836000  16.8290   
2006-07-06      13.65   -0.035336  19.114446  14.654  15.315333  16.6215   
2006-07-07      13.97    0.023443  19.114446  14.463  15.186667  16.4025   
2006-07-10      14.02    0.003579  19.114446  14.276  14.971333  16.1975   

             sma 50  sma 100    sma 150   sma 200  ...  c_3_neg_returns  \
Date                                               ...                    
2006-07-03  15.2390  13.5626  12.981600  13.09455  ...                0   
2006-07-05  15.2870  13.5729  12.997000  13.10920  ...                0   
2006-07-06  15.3250  13.5807  13.008733  13.11675  ...                0   
2006-07-07  15.3692  13.5869  13.021467  13.12340  ...                0   
2006-07-10  15.4128  13.6046  13.040000  13.12455  ...                0   

            >b_upper  <b_lower  Friday  Monday  Thursday  Tuesday  Wednesday  \
Date                                                                           
2006-07-03         0         0       0       1         0        0          0   
2006-07-05         0         0       0       0         0        0          1   
2006-07-06         0         0       0       0         1        0          0   
2006-07-07         0         0       1       0         0        0          0   
2006-07-10         0         0       0       1         0        0          0   

            Signal  Strategy Returns  
Date                                  
2006-07-03     0.0               NaN  
2006-07-05     1.0          0.000000  
2006-07-06     0.0         -0.035336  
2006-07-07     1.0          0.000000  
2006-07-10     1.0          0.003579  

[5 rows x 46 columns]

vix close  vix return       mean  sma 10     sma 15   sma 20  \
Date                                                                       
2021-09-27  18.760000    0.056901  19.114446  20.322  19.896000  19.0020   
2021-09-28  23.250000    0.239339  19.114446  20.701  20.236667  19.3550   
2021-09-29  22.559999   -0.029677  19.114446  21.139  20.543333  19.6590   
2021-09-30  23.139999    0.025709  19.114446  21.584  20.832667  20.0105   
2021-10-01  21.100000   -0.088159  19.114446  21.613  20.842667  20.2450   

             sma 50  sma 100    sma 150   sma 200  ...  c_3_neg_returns  \
Date                                               ...                    
2021-09-27  18.3620  18.1287  18.774133  19.97435  ...                0   
2021-09-28  18.3770  18.1773  18.786867  19.97800  ...                0   
2021-09-29  18.4336  18.2360  18.744667  19.97425  ...                0   
2021-09-30  18.5382  18.2708  18.712600  19.96635  ...                0   
2021-10-01  18.6064  18.2634  18.697600  19.95740  ...                0   

            >b_upper  <b_lower  Friday  Monday  Thursday  Tuesday  Wednesday  \
Date                                                                           
2021-09-27         0         0       0       1         0        0          0   
2021-09-28         0         0       0       0         0        1          0   
2021-09-29         0         0       0       0         0        0          1   
2021-09-30         0         0       0       0         1        0          0   
2021-10-01         0         0       1       0         0        0          0   

            Signal  Strategy Returns  
Date                                  
2021-09-27     1.0          0.000000  
2021-09-28     1.0          0.239339  
2021-09-29     0.0         -0.029677  
2021-09-30     1.0          0.000000  
2021-10-01     0.0         -0.088159  

[5 rows x 46 columns]

In [445]:
# Check if the data is finite or has nans, etc.
display(np.all(np.isfinite(technical_variables_enhanced_df)))

False

In [446]:
# technical_variables_enhanced_df
X = technical_variables_enhanced_df.drop(columns=["vix close", "vix return", "mean", "Signal", "Strategy Returns"]) 

# Assign a copy of the sma_fast and sma_slow columns to a features DataFrame called X
X = X.shift()
display(np.all(np.isfinite(X)))
X = X.iloc[1:,:]
display(np.all(np.isfinite(X)))

# Review the DataFrame
X.head()

False

True

sma 10     sma 15   sma 20   sma 50  sma 100    sma 150   sma 200  \
Date                                                                            
2006-07-05  15.095  16.480000  16.9885  15.2390  13.5626  12.981600  13.09455   
2006-07-06  14.841  15.836000  16.8290  15.2870  13.5729  12.997000  13.10920   
2006-07-07  14.654  15.315333  16.6215  15.3250  13.5807  13.008733  13.11675   
2006-07-10  14.463  15.186667  16.4025  15.3692  13.5869  13.021467  13.12340   
2006-07-11  14.276  14.971333  16.1975  15.4128  13.6046  13.040000  13.12455   

             sma 250  a15  a50  ...  c_3_200  c_3_pos_returns  \
Date                            ...                             
2006-07-05  12.91576  0.0  0.0  ...      0.0              0.0   
2006-07-06  12.92240  0.0  0.0  ...      0.0              0.0   
2006-07-07  12.93120  0.0  0.0  ...      0.0              0.0   
2006-07-10  12.94196  0.0  0.0  ...      1.0              0.0   
2006-07-11  12.95424  0.0  0.0  ...      1.0              0.0   

            c_3_neg_returns  >b_upper  <b_lower  Friday  Monday  Thursday  \
Date                                                                        
2006-07-05              0.0       0.0       0.0     0.0     1.0       0.0   
2006-07-06              0.0       0.0       0.0     0.0     0.0       0.0   
2006-07-07              0.0       0.0       0.0     0.0     0.0       1.0   
2006-07-10              0.0       0.0       0.0     1.0     0.0       0.0   
2006-07-11              0.0       0.0       0.0     0.0     1.0       0.0   

            Tuesday  Wednesday  
Date                            
2006-07-05      0.0        0.0  
2006-07-06      0.0        1.0  
2006-07-07      0.0        0.0  
2006-07-10      0.0        0.0  
2006-07-11      0.0        0.0  

[5 rows x 41 columns]

In [447]:
# Check if the data is finite or has nans, etc.
display(np.all(np.isfinite(X)))
display(np.any(np.isnan(X)))

True

False

In [448]:
# Create the target set selecting the Signal column and assiging it to y
y = technical_variables_enhanced_df['Signal']
y = y.iloc[1:]

# Review the value counts
display(y.value_counts())
display(y.head())

0.0    2067
1.0    1772
Name: Signal, dtype: int64

Date
2006-07-05    1.0
2006-07-06    0.0
2006-07-07    1.0
2006-07-10    1.0
2006-07-11    0.0
Name: Signal, dtype: float64

In [449]:
# Select the start of the training period
training_begin = X.index.min()

# Display the training begin date
print(training_begin)

2006-07-05 00:00:00


In [450]:
# Select the ending period for the training data with an offset of 3 months
training_end = training_begin + DateOffset(months=training_months)

# Display the training end date
print(training_end)

2016-07-05 00:00:00


In [451]:
# Generate the X_train and y_train DataFrames
X_train = X.loc[training_begin:training_end]
y_train = y.loc[training_begin:training_end]

# Review the X_train DataFrame
display(X_train.head())
display(X_train.tail())
display(X_train.shape)
display(y_train.shape)
display(np.any(np.isnan(X_train)))
display(np.all(np.isfinite(X_train)))

sma 10     sma 15   sma 20   sma 50  sma 100    sma 150   sma 200  \
Date                                                                            
2006-07-05  15.095  16.480000  16.9885  15.2390  13.5626  12.981600  13.09455   
2006-07-06  14.841  15.836000  16.8290  15.2870  13.5729  12.997000  13.10920   
2006-07-07  14.654  15.315333  16.6215  15.3250  13.5807  13.008733  13.11675   
2006-07-10  14.463  15.186667  16.4025  15.3692  13.5869  13.021467  13.12340   
2006-07-11  14.276  14.971333  16.1975  15.4128  13.6046  13.040000  13.12455   

             sma 250  a15  a50  ...  c_3_200  c_3_pos_returns  \
Date                            ...                             
2006-07-05  12.91576  0.0  0.0  ...      0.0              0.0   
2006-07-06  12.92240  0.0  0.0  ...      0.0              0.0   
2006-07-07  12.93120  0.0  0.0  ...      0.0              0.0   
2006-07-10  12.94196  0.0  0.0  ...      1.0              0.0   
2006-07-11  12.95424  0.0  0.0  ...      1.0              0.0   

            c_3_neg_returns  >b_upper  <b_lower  Friday  Monday  Thursday  \
Date                                                                        
2006-07-05              0.0       0.0       0.0     0.0     1.0       0.0   
2006-07-06              0.0       0.0       0.0     0.0     0.0       0.0   
2006-07-07              0.0       0.0       0.0     0.0     0.0       1.0   
2006-07-10              0.0       0.0       0.0     1.0     0.0       0.0   
2006-07-11              0.0       0.0       0.0     0.0     1.0       0.0   

            Tuesday  Wednesday  
Date                            
2006-07-05      0.0        0.0  
2006-07-06      0.0        1.0  
2006-07-07      0.0        0.0  
2006-07-10      0.0        0.0  
2006-07-11      0.0        0.0  

[5 rows x 41 columns]

sma 10     sma 15   sma 20   sma 50  sma 100    sma 150   sma 200  \
Date                                                                            
2016-06-28  20.430  19.004667  17.7105  15.8340  16.8765  17.946133  18.08775   
2016-06-29  20.255  19.318000  17.9385  15.9420  16.8456  17.968000  18.06550   
2016-06-30  19.905  19.488667  18.0605  16.0100  16.7782  17.974800  18.02745   
2016-07-01  19.531  19.554667  18.1605  16.0570  16.6745  17.972800  17.99290   
2016-07-05  19.067  19.404000  18.2255  16.0734  16.5568  17.970000  17.96000   

             sma 250  a15  a50  ...  c_3_200  c_3_pos_returns  \
Date                            ...                             
2016-06-28  18.11080  1.0  1.0  ...      0.0              0.0   
2016-06-29  18.12144  0.0  1.0  ...      1.0              0.0   
2016-06-30  18.12084  0.0  1.0  ...      0.0              0.0   
2016-07-01  18.11532  0.0  0.0  ...      0.0              0.0   
2016-07-05  18.11004  0.0  0.0  ...      0.0              0.0   

            c_3_neg_returns  >b_upper  <b_lower  Friday  Monday  Thursday  \
Date                                                                        
2016-06-28              0.0       0.0       0.0     0.0     1.0       0.0   
2016-06-29              0.0       0.0       0.0     0.0     0.0       0.0   
2016-06-30              1.0       0.0       0.0     0.0     0.0       0.0   
2016-07-01              1.0       0.0       0.0     0.0     0.0       1.0   
2016-07-05              1.0       0.0       0.0     1.0     0.0       0.0   

            Tuesday  Wednesday  
Date                            
2016-06-28      0.0        0.0  
2016-06-29      1.0        0.0  
2016-06-30      0.0        1.0  
2016-07-01      0.0        0.0  
2016-07-05      0.0        0.0  

[5 rows x 41 columns]

(2518, 41)

(2518,)

False

True

In [452]:
# Use RandomOverSampler to resample the dataset using random_state=1
ros = RandomOverSampler(random_state = 1)
X_train_resampled, y_train_resampled = ros.fit_resample(X_train, y_train)

display(y_train_resampled.value_counts())

0.0    1354
1.0    1354
Name: Signal, dtype: int64

In [453]:
# Generate the X_test and y_test DataFrames
X_test = X.loc[training_end+DateOffset(days=1):]
y_test = y.loc[training_end+DateOffset(days=1):]

# Review the X_test DataFrame
display(X_test.head())
display(X_test.tail())

sma 10     sma 15   sma 20   sma 50  sma 100    sma 150   sma 200  \
Date                                                                            
2016-07-06  18.788  19.044667  18.3220  16.1206  16.4497  17.973067  17.93220   
2016-07-07  18.436  18.675333  18.3675  16.1382  16.3179  17.965267  17.89560   
2016-07-08  17.795  18.316667  18.4015  16.1542  16.2115  17.965867  17.86870   
2016-07-11  17.390  17.905333  18.3295  16.1428  16.1024  17.947800  17.82250   
2016-07-12  16.168  17.514000  18.1550  16.1092  16.0147  17.917333  17.77955   

             sma 250  a15  a50  ...  c_3_200  c_3_pos_returns  \
Date                            ...                             
2016-07-06  18.09372  0.0  0.0  ...      0.0              0.0   
2016-07-07  18.07368  0.0  0.0  ...      0.0              0.0   
2016-07-08  18.06540  0.0  0.0  ...      0.0              0.0   
2016-07-11  18.06260  0.0  0.0  ...      0.0              0.0   
2016-07-12  18.06328  0.0  0.0  ...      0.0              0.0   

            c_3_neg_returns  >b_upper  <b_lower  Friday  Monday  Thursday  \
Date                                                                        
2016-07-06              0.0       0.0       0.0     0.0     0.0       0.0   
2016-07-07              0.0       0.0       0.0     0.0     0.0       0.0   
2016-07-08              0.0       0.0       0.0     0.0     0.0       1.0   
2016-07-11              1.0       0.0       0.0     1.0     0.0       0.0   
2016-07-12              0.0       0.0       0.0     0.0     1.0       0.0   

            Tuesday  Wednesday  
Date                            
2016-07-06      1.0        0.0  
2016-07-07      0.0        1.0  
2016-07-08      0.0        0.0  
2016-07-11      0.0        0.0  
2016-07-12      0.0        0.0  

[5 rows x 41 columns]

sma 10     sma 15   sma 20   sma 50  sma 100    sma 150   sma 200  \
Date                                                                            
2021-09-27  20.383  19.739333  18.8835  18.3558  18.1326  18.803133  19.99190   
2021-09-28  20.322  19.896000  19.0020  18.3620  18.1287  18.774133  19.97435   
2021-09-29  20.701  20.236667  19.3550  18.3770  18.1773  18.786867  19.97800   
2021-09-30  21.139  20.543333  19.6590  18.4336  18.2360  18.744667  19.97425   
2021-10-01  21.584  20.832667  20.0105  18.5382  18.2708  18.712600  19.96635   

             sma 250  a15  a50  ...  c_3_200  c_3_pos_returns  \
Date                            ...                             
2021-09-27  21.29828  0.0  0.0  ...      0.0              0.0   
2021-09-28  21.26824  0.0  1.0  ...      0.0              0.0   
2021-09-29  21.25576  1.0  1.0  ...      0.0              0.0   
2021-09-30  21.23920  1.0  1.0  ...      0.0              0.0   
2021-10-01  21.22124  1.0  1.0  ...      1.0              0.0   

            c_3_neg_returns  >b_upper  <b_lower  Friday  Monday  Thursday  \
Date                                                                        
2021-09-27              1.0       0.0       0.0     1.0     0.0       0.0   
2021-09-28              0.0       0.0       0.0     0.0     1.0       0.0   
2021-09-29              0.0       0.0       0.0     0.0     0.0       0.0   
2021-09-30              0.0       0.0       0.0     0.0     0.0       0.0   
2021-10-01              0.0       0.0       0.0     0.0     0.0       1.0   

            Tuesday  Wednesday  
Date                            
2021-09-27      0.0        0.0  
2021-09-28      0.0        0.0  
2021-09-29      1.0        0.0  
2021-09-30      0.0        1.0  
2021-10-01      0.0        0.0  

[5 rows x 41 columns]

In [454]:
# Scale the features DataFrames

# Create a StandardScaler instance
scaler = StandardScaler()

# Apply the scaler model to fit the X-train data
X_scaler = scaler.fit(X_train_resampled)

# Transform the X_train and X_test DataFrames using the X_scaler
X_train_scaled = X_scaler.transform(X_train_resampled)
X_test_scaled = X_scaler.transform(X_test)
display(np.any(np.isnan(X_train_scaled)))
display(np.all(np.isfinite(X_train_scaled)))

False

True

In [455]:
# Initiate the AdaBoost model
# Initiate the model instance
adaboost_model = AdaBoostClassifier(n_estimators=adaboost_estimators)
adaboost_model
# Fit the model 
adaboost_model = adaboost_model.fit(X_train_scaled, y_train_resampled)

pred_adaboost = adaboost_model.predict(X_test_scaled)
# Use a classification report to evaluate the model using the predictions and testing data
adaboost_report = classification_report(y_test, pred_adaboost)

# Print the classification report
print("         AdaBoost Classification Report")
print(adaboost_report)

         AdaBoost Classification Report
              precision    recall  f1-score   support

         0.0       0.59      0.50      0.54       713
         1.0       0.51      0.60      0.55       608

    accuracy                           0.55      1321
   macro avg       0.55      0.55      0.55      1321
weighted avg       0.55      0.55      0.55      1321



In [456]:
# Check the feature importance of the model.
importance = adaboost_model.feature_importances_
# summarize feature importance
feature_importance_list = []
x_test_columns = X_test.columns
# Print the feature importance
for i,v in enumerate(importance):
	print(f'Feature: {i} Score: {v} Name {x_test_columns[i]}')

Feature: 0 Score: 0.13953488372093023 Name sma 10
Feature: 1 Score: 0.11627906976744186 Name sma 15
Feature: 2 Score: 0.046511627906976744 Name sma 20
Feature: 3 Score: 0.046511627906976744 Name sma 50
Feature: 4 Score: 0.046511627906976744 Name sma 100
Feature: 5 Score: 0.13953488372093023 Name sma 150
Feature: 6 Score: 0.06976744186046512 Name sma 200
Feature: 7 Score: 0.13953488372093023 Name sma 250
Feature: 8 Score: 0.0 Name a15
Feature: 9 Score: 0.0 Name a50
Feature: 10 Score: 0.0 Name a100
Feature: 11 Score: 0.0 Name a150
Feature: 12 Score: 0.0 Name a200
Feature: 13 Score: 0.0 Name b15
Feature: 14 Score: 0.023255813953488372 Name b50
Feature: 15 Score: 0.0 Name b100
Feature: 16 Score: 0.0 Name b150
Feature: 17 Score: 0.0 Name b200
Feature: 18 Score: 0.0 Name vix_pos_return
Feature: 19 Score: 0.0 Name vix_neg_return
Feature: 20 Score: 0.0 Name c_1_15
Feature: 21 Score: 0.0 Name c_1_50
Feature: 22 Score: 0.023255813953488372 Name c_1_100
Feature: 23 Score: 0.046511627906976744 Nam

In [457]:
# Create a new empty predictions DataFrame.

# Create a predictions DataFrame
adaboost_predictions_df = pd.DataFrame(index = X_test.index)

# Add the DTC model predictions to the DataFrame
adaboost_predictions_df['Predicted'] = pred_adaboost

# Add the actual returns to the DataFrame
adaboost_predictions_df['Actual Returns'] = technical_variables_enhanced_df.loc[training_end+DateOffset(days=1):,'vix return']

# Add the strategy returns to the DataFrame
adaboost_predictions_df['Strategy Returns'] = adaboost_predictions_df['Actual Returns'] * adaboost_predictions_df['Predicted'].shift()

# Review the DataFrame
display(adaboost_predictions_df.head())
display(adaboost_predictions_df.tail())

Predicted  Actual Returns  Strategy Returns
Date                                                   
2016-07-06        1.0       -0.039795               NaN
2016-07-07        1.0       -0.013369         -0.013369
2016-07-08        1.0       -0.105691         -0.105691
2016-07-11        1.0        0.025758          0.025758
2016-07-12        1.0        0.000739          0.000739

Predicted  Actual Returns  Strategy Returns
Date                                                   
2021-09-27        1.0        0.056901          0.000000
2021-09-28        0.0        0.239339          0.239339
2021-09-29        0.0       -0.029677         -0.000000
2021-09-30        0.0        0.025709          0.000000
2021-10-01        0.0       -0.088159         -0.000000

In [458]:
# Figure out the actual returns, strategy returns, the shifted strategy returns, strategy returns actual
adaboost_strategy_returns_hvplot = (1 + adaboost_predictions_df['Strategy Returns']).cumprod().hvplot(title = "Adaboost Strategy Returns - ROI 4056% (42X)")
adaboost_actual_returns_hvplot = (1 + adaboost_predictions_df['Actual Returns']).cumprod().hvplot()
# Plot the actual returns versus the strategy returns
adaboost_strategy_returns_hvplot

:Curve   [Date]   (Strategy Returns)

In [459]:
# Figure out the ROI of the strategy returns
cum_prod_df = (1 + adaboost_predictions_df['Strategy Returns']).cumprod()
print(f"ROI value {cum_prod_df[-1]}")
roi = (cum_prod_df[-1] - 1) * 100
print(f"ROI is {roi:.02f}%")
print(f"final revenue is ${cum_prod_df[-1]:.02f} for an initial investment is $1")

ROI value 41.55570752037431
ROI is 4055.57%
final revenue is $41.56 for an initial investment is $1


In [460]:
# Code to fine tune the model 
if run_multiple_tuning_iterations == True: 
    # Create a predictions DataFrame
    adaboost_predictions_df = pd.DataFrame(index = X_test.index)
    adaboost_model_results_df = pd.DataFrame()
    plot_list = []
    # for num_estimators in range (1,100, 1):
    for num_estimators in [43, 23, 24, 46, 45, 29, 30, 25, 41,47, 14, 64, 66, 34, 37, 36]:
        print(num_estimators)
        adaboost_model = AdaBoostClassifier(n_estimators=num_estimators)

        # Fit the model 
        adaboost_model = adaboost_model.fit(X_train_scaled, y_train_resampled)
        pred_adaboost = adaboost_model.predict(X_test_scaled)
        # Use a classification report to evaluate the model using the predictions and testing data
        adaboost_report = classification_report(y_test, pred_adaboost)

        f1_score_1 = f1_score(y_test, pred_adaboost, pos_label=1)
        f1_score_0 = f1_score(y_test, pred_adaboost, pos_label=0)
        recall_score_1 = recall_score(y_test, pred_adaboost, pos_label=1)
        recall_score_0 = recall_score(y_test, pred_adaboost, pos_label=0)
        accuracy_score_model = accuracy_score(y_test, pred_adaboost)
        
        # Add the DTC model predictions to the DataFrame
        adaboost_predictions_df['Predicted'] = pred_adaboost

        # Add the actual returns to the DataFrame
        adaboost_predictions_df['Actual Returns'] = technical_variables_enhanced_df.loc[training_end+DateOffset(days=1):,'vix return']

        # Add the strategy returns to the DataFrame
        adaboost_predictions_df['Strategy Returns'] = adaboost_predictions_df['Actual Returns'] * adaboost_predictions_df['Predicted'].shift()
        
        adaboost_predictions_df["Cum Returns"] = (1 + adaboost_predictions_df['Strategy Returns']).cumprod()
        
        adaboost_model_results_df.loc[num_estimators, "Accuracy"] = accuracy_score_model
        adaboost_model_results_df.loc[num_estimators, "ROI"] = adaboost_predictions_df["Cum Returns"][-1] -1
        adaboost_model_results_df.loc[num_estimators, "F1 score 1"] = f1_score_1
        adaboost_model_results_df.loc[num_estimators, "F1 score 0"] = f1_score_0
        adaboost_model_results_df.loc[num_estimators, "Recall score 1"] = recall_score_1
        adaboost_model_results_df.loc[num_estimators, "Recall score 0"] = recall_score_0
        
        display(adaboost_predictions_df["Cum Returns"].hvplot.line(subplots=True))
        #if  accuracy_score_model >= .50 and f1_score_1 >= .50 and recall_score_1 >= .50:
        #    print(f"estimators {num_estimators}")
        #    print("         AdaBoost Classification Report")
        #    print(adaboost_report)

In [461]:
# Check the model tuning output results - sort by accuracy
if run_multiple_tuning_iterations == True: 
    adaboost_model_results_df.sort_values(by="Accuracy", ascending=False)

In [462]:
# Check the model tuning output results - sort by ROI
if run_multiple_tuning_iterations == True: 
    adaboost_model_results_df.sort_values(by="ROI", ascending=False).head(20)